## Grid Objectives
Iterating between min and max for each column

### Glossary
- **task**: Refers to the set of values (row) and corresponding keys to be aimed at sequentially.
- **objective**: Refers to one key (column) and respective value to be aimed at simultaneously during a task.
- **experiment**: Refers to one file containing a multiple of objectives and tasks for a fixed number of each, respectively. 

In [1]:
import itertools
import json
import numpy as np
import os
import pandas as pd

In [2]:
#Features between 0 and 1: 
normalized_feature_names = ['ratio_unique_traces_per_trace', 'trace_len_hist1', 'trace_len_hist2',
                            'trace_len_hist3', 'trace_len_hist4', 'trace_len_hist5', 'trace_len_hist7',
                            'trace_len_hist8', 'trace_len_hist9', 'ratio_most_common_variant', 
                            'ratio_top_1_variants', 'ratio_top_5_variants', 'ratio_top_10_variants', 
                            'ratio_top_20_variants', 'ratio_top_50_variants', 'ratio_top_75_variants', 
                            'epa_normalized_variant_entropy', 'epa_normalized_sequence_entropy', 
                            'epa_normalized_sequence_entropy_linear_forgetting', 'epa_normalized_sequence_entropy_exponential_forgetting']

normalized_feature_names = ['ratio_unique_traces_per_trace', 'ratio_most_common_variant', 
                            'ratio_top_10_variants', 'epa_normalized_variant_entropy', 'epa_normalized_sequence_entropy', 
                            'epa_normalized_sequence_entropy_linear_forgetting', 'epa_normalized_sequence_entropy_exponential_forgetting']

def abbrev_obj_keys(obj_keys):
    abbreviated_keys = []
    for obj_key in obj_keys:
        key_slices = obj_key.split("_")
        chars = []
        for key_slice in key_slices:
            for idx, single_char in enumerate(key_slice):
                if idx == 0 or single_char.isdigit():
                    chars.append(single_char)
        abbreviated_key = ''.join(chars)
        abbreviated_keys.append(abbreviated_key)
    return '_'.join(abbreviated_keys) 

In [6]:
def write_generator_experiment(experiment_path, objectives=["ratio_top_20_variants", "epa_normalized_sequence_entropy_linear_forgetting"]):
    first_dir = os.path.split(experiment_path[3:])[-1].replace(".csv","")
    second_dir = first_dir.replace("grid_","").replace("objectives","")

    experiment = [
      {
        'pipeline_step': 'event_logs_generation',
        'output_path':'output/generated/grid_2obj',
        'generator_params': {
          "experiment": {"input_path": experiment_path[3:],
            "objectives": objectives},
          'config_space': {
            'mode': [5, 20],
            'sequence': [0.01, 1],
            'choice': [0.01, 1],
            'parallel': [0.01, 1],
            'loop': [0.01, 1],
            'silent': [0.01, 1],
            'lt_dependency': [0.01, 1],
            'num_traces': [10, 10001],
            'duplicate': [0],
            'or': [0]
          },
          'n_trials': 200
        }
      },
      {
        'pipeline_step': 'feature_extraction',
        'input_path': os.path.join('output','features', 'generated', 'grid_2obj', first_dir, second_dir),
        'feature_params': {'feature_set':['simple_stats', 'trace_length', 'trace_variant', 'activities', 'start_activities', 'end_activities', 'eventropies', 'epa_based']},
        'output_path': 'output/plots',
        'real_eventlog_path': 'data/34_bpic_features.csv',
        'plot_type': 'boxplot'
  }
    ]

    #print("EXPERIMENT:", experiment[1]['input_path'])
    output_path = os.path.join('..', 'config_files','algorithm','grid_2obj')
    os.makedirs(output_path, exist_ok=True)
    output_path = os.path.join(output_path, f'generator_{os.path.split(experiment_path)[-1].split(".")[0]}.json') 
    with open(output_path, 'w') as f:
        json.dump(experiment, f, ensure_ascii=False)
    print(f"Saved experiment config in {output_path}")
    
    return experiment

def create_objectives_grid(objectives, n_para_obj=2):
    parameters_o = "objectives, "
    if n_para_obj==1:
        experiments = [[exp] for exp in objectives]
    else:
        experiments = eval(f"[exp for exp in list(itertools.product({(parameters_o*n_para_obj)[:-2]})) if exp[0]!=exp[1]]")
    experiments = list(set([tuple(sorted(exp)) for exp in experiments]))
    print(len(experiments), experiments)
    
    parameters = "np.around(np.arange(0, 1.1,0.1),2), "
    tasks = eval(f"list(itertools.product({(parameters*n_para_obj)[:-2]}))")
    tasks = [(f'task_{i+1}',)+task for i, task in enumerate(tasks)]
    print(len(tasks))
    for exp in experiments:
        df = pd.DataFrame(data=tasks, columns=["task", *exp])
        experiment_path = os.path.join('..','data', 'grid_2obj')
        os.makedirs(experiment_path, exist_ok=True)
        experiment_path = os.path.join(experiment_path, f"grid_{len(df.columns)-1}objectives_{abbrev_obj_keys(exp)}.csv") 
        df.to_csv(experiment_path, index=False)
        print(f"Saved experiment in {experiment_path}")
        write_generator_experiment(experiment_path, objectives=exp)
    #df.to_csv(f"../data/grid_{}objectives_{abbrev_obj_keys(objectives.tolist())}.csv" ,index=False)
        
exp_test = create_objectives_grid(normalized_feature_names, n_para_obj=2)        
print(exp_test)

21 [('epa_normalized_sequence_entropy_linear_forgetting', 'ratio_top_10_variants'), ('epa_normalized_sequence_entropy_exponential_forgetting', 'ratio_unique_traces_per_trace'), ('ratio_top_10_variants', 'ratio_unique_traces_per_trace'), ('epa_normalized_sequence_entropy', 'ratio_most_common_variant'), ('ratio_most_common_variant', 'ratio_top_10_variants'), ('epa_normalized_sequence_entropy', 'epa_normalized_sequence_entropy_linear_forgetting'), ('epa_normalized_sequence_entropy', 'epa_normalized_variant_entropy'), ('epa_normalized_sequence_entropy_exponential_forgetting', 'ratio_most_common_variant'), ('epa_normalized_variant_entropy', 'ratio_top_10_variants'), ('epa_normalized_sequence_entropy_exponential_forgetting', 'epa_normalized_sequence_entropy_linear_forgetting'), ('epa_normalized_sequence_entropy_exponential_forgetting', 'epa_normalized_variant_entropy'), ('epa_normalized_sequence_entropy_linear_forgetting', 'ratio_unique_traces_per_trace'), ('epa_normalized_sequence_entropy',

### Helper prototypes

In [11]:
df = pd.DataFrame(columns=["log","ratio_top_20_variants", "epa_normalized_sequence_entropy_linear_forgetting"])    

In [12]:
k=0
for i in np.arange(0, 1.1,0.2):
    for j in np.arange(0,0.55,0.1):
        k+=1
        new_entry = pd.Series({'log':f"objective_{k}", "ratio_top_20_variants":round(i,1),
                   "epa_normalized_sequence_entropy_linear_forgetting":round(j,1)})
        df = pd.concat([
                df, 
                pd.DataFrame([new_entry], columns=new_entry.index)]
           ).reset_index(drop=True)
    

In [13]:
df.to_csv("../data/grid_objectives.csv" ,index=False)

In [6]:
df

log  ratio_top_20_variants   
0    objective_1                    0.0  \
1    objective_2                    0.0   
2    objective_3                    0.0   
3    objective_4                    0.0   
4    objective_5                    0.0   
5    objective_6                    0.0   
6    objective_7                    0.2   
7    objective_8                    0.2   
8    objective_9                    0.2   
9   objective_10                    0.2   
10  objective_11                    0.2   
11  objective_12                    0.2   
12  objective_13                    0.4   
13  objective_14                    0.4   
14  objective_15                    0.4   
15  objective_16                    0.4   
16  objective_17                    0.4   
17  objective_18                    0.4   
18  objective_19                    0.6   
19  objective_20                    0.6   
20  objective_21                    0.6   
21  objective_22                    0.6   
22  objective_23                    0.6   
23  objective_24                    0.6   
24  objective_25                    0.8   
25  objective_26                    0.8   
26  objective_27                    0.8   
27  objective_28                    0.8   
28  objective_29                    0.8   
29  objective_30                    0.8   
30  objective_31                    1.0   
31  objective_32                    1.0   
32  objective_33                    1.0   
33  objective_34                    1.0   
34  objective_35                    1.0   
35  objective_36                    1.0   

    normalized_sequence_entropy_linear_forgetting  
0                                             0.0  
1                                             0.1  
2                                             0.2  
3                                             0.3  
4                                             0.4  
5                                             0.5  
6                                             0.0  
7                                             0.1  
8                                             0.2  
9                                             0.3  
10                                            0.4  
11                                            0.5  
12                                            0.0  
13                                            0.1  
14                                            0.2  
15                                            0.3  
16                                            0.4  
17                                            0.5  
18                                            0.0  
19                                            0.1  
20                                            0.2  
21                                            0.3  
22                                            0.4  
23                                            0.5  
24                                            0.0  
25                                            0.1  
26                                            0.2  
27                                            0.3  
28                                            0.4  
29                                            0.5  
30                                            0.0  
31                                            0.1  
32                                            0.2  
33                                            0.3  
34                                            0.4  
35                                            0.5

## Objectives from real logs
(Feature selection)

In [20]:
bpic_features = pd.read_csv("../data/34_bpic_features.csv", index_col=None)
#bpic_features = pd.read_csv("../gedi/output/features/real_event_logs.csv", index_col=None)

#bpic_features = bpic_features.drop(['Unnamed: 0'], axis=1)
print(bpic_features.shape)
print(len(bpic_features), " Event-Logs: ", bpic_features.sort_values('log')['log'].unique())

#bpic_features.rename(columns={"variant_entropy":"epa_variant_entropy", "normalized_variant_entropy":"epa_normalized_variant_entropy", "sequence_entropy":"epa_sequence_entropy", "normalized_sequence_entropy":"epa_normalized_sequence_entropy", "sequence_entropy_linear_forgetting":"epa_sequence_entropy_linear_forgetting", "normalized_sequence_entropy_linear_forgetting":"epa_normalized_sequence_entropy_linear_forgetting", "sequence_entropy_exponential_forgetting":"epa_sequence_entropy_exponential_forgetting", "normalized_sequence_entropy_exponential_forgetting":"epa_normalized_sequence_entropy_exponential_forgetting"},
#          errors="raise", inplace=True)

bpic_features.head()
#bpic_features.to_csv("../data/34_bpic_features.csv", index=False)

(34, 178)
34  Event-Logs:  ['BPI2016_Complaints' 'BPI2016_Questions' 'BPI2016_Werkmap_Messages'
 'BPIC15_1' 'BPIC15_2' 'BPIC15_3' 'BPIC15_4' 'BPIC15_5'
 'BPI_Challenge_2012' 'BPI_Challenge_2013_closed_problems'
 'BPI_Challenge_2013_incidents' 'BPI_Challenge_2013_open_problems'
 'BPI_Challenge_2017' 'BPI_Challenge_2017_Offer_log' 'BPI_Challenge_2018'
 'BPI_Challenge_2019' 'CoSeLoG_WABO_1' 'CoSeLoG_WABO_2' 'CoSeLoG_WABO_3'
 'CoSeLoG_WABO_4' 'CoSeLoG_WABO_5' 'Detail_Change'
 'Detail_Incident_Activity' 'Detail_Interaction' 'DomesticDeclarations'
 'Hospital_log' 'InternationalDeclarations' 'PermitLog'
 'PrepaidTravelCost' 'Receipt_WABO_CoSeLoG' 'RequestForPayment'
 'Road_Traffic_Fine_Management_Process' 'Sepsis_Cases_Event_Log' 'finale']


log  n_traces  n_unique_traces   
0              BPIC15_2       832              828  \
1    BPI_Challenge_2018     43809            28457   
2  Receipt_WABO_CoSeLoG      1434              116   
3              BPIC15_3      1409             1349   
4    BPI_Challenge_2019    251734            11973   

   ratio_unique_traces_per_trace  trace_len_min  trace_len_max   
0                       0.995192              1            132  \
1                       0.649570             24           2973   
2                       0.080893              1             25   
3                       0.957417              3            124   
4                       0.047562              1            990   

   trace_len_mean  trace_len_median  trace_len_mode  trace_len_std   
0       53.310096              54.0              61      19.894977  \
1       57.391541              49.0              49      34.872131   
2        5.981172               6.0               6       2.166129   
3       42.356991              42.0              44      16.138406   
4        6.339720               5.0               5      13.057417   

   trace_len_variance  trace_len_q1  trace_len_q3  trace_len_iqr   
0          395.810090          44.0          62.0           18.0  \
1         1216.065487          44.0          59.0           15.0   
2            4.692114           6.0           6.0            0.0   
3          260.448143          38.0          47.0            9.0   
4          170.496137           5.0           6.0            1.0   

   trace_len_geometric_mean  trace_len_geometric_std  trace_len_harmonic_mean   
0                 48.150111                 1.695311                37.583741  \
1                 53.775008                 1.367397                51.651502   
2                  5.414708                 1.704965                 4.356445   
3                 37.637731                 1.786726                29.092933   
4                  5.173569                 1.635822                 4.592844   

   trace_len_skewness  trace_len_kurtosis  trace_len_coefficient_variation   
0            0.054138            0.804992                         0.373193  \
1           26.126459         1720.399665                         0.607618   
2            1.276525           12.296006                         0.362158   
3           -0.009541            1.543369                         0.381009   
4           22.132989          753.772202                         2.059621   

   trace_len_entropy  trace_len_hist1  trace_len_hist2  trace_len_hist3   
0           6.646715         0.003853         0.004863     4.679243e-03  \
1          10.598758         0.003385         0.000005     9.288448e-07   
2           7.197193         0.036030         0.008136     3.411204e-01   
3           7.167153         0.006921         0.004340     1.630604e-02   
4          12.044057         0.010078         0.000020     9.559579e-06   

   trace_len_hist4  trace_len_hist5  trace_len_hist6  trace_len_hist7   
0         0.023947     2.376321e-02     8.257487e-03         0.004771  \
1         0.000000     0.000000e+00     0.000000e+00         0.000000   
2         0.023536     3.777313e-03     1.743375e-03         0.000291   
3         0.036953     1.173096e-02     4.105837e-03         0.001584   
4         0.000003     3.614967e-07     1.606652e-07         0.000000   

   trace_len_hist8  trace_len_hist9  trace_len_hist10   
0     1.376248e-03     6.422490e-04      1.834997e-04  \
1     0.000000e+00     7.740373e-08      7.740373e-08   
2     1.452813e-03     0.000000e+00      5.811251e-04   
3     5.278933e-04     1.173096e-04      5.865481e-05   
4     4.016630e-08     8.033260e-08      8.033260e-08   

   trace_len_skewness_hist  trace_len_kurtosis_hist   
0                 0.054138                 0.804992  \
1                26.126459              1720.399665   
2                 1.276525                12.296006   
3                -0.009541                 1.543369   
4   

In [21]:
bpic_stats = bpic_features.describe().transpose()
normalized_feature_names = bpic_stats[(bpic_stats['min']>=0)&(bpic_stats['max']<=1)].index.to_list() 
normalized_feature_names = ['ratio_unique_traces_per_trace', 'ratio_most_common_variant', 
                            'ratio_top_10_variants', 'epa_normalized_variant_entropy', 'epa_normalized_sequence_entropy', 
                            'epa_normalized_sequence_entropy_linear_forgetting', 'epa_normalized_sequence_entropy_exponential_forgetting']
print(normalized_feature_names)
bpic_features[['log']+normalized_feature_names]

['ratio_unique_traces_per_trace', 'ratio_most_common_variant', 'ratio_top_10_variants', 'epa_normalized_variant_entropy', 'epa_normalized_sequence_entropy', 'epa_normalized_sequence_entropy_linear_forgetting', 'epa_normalized_sequence_entropy_exponential_forgetting']


log  ratio_unique_traces_per_trace   
0                               BPIC15_2                       0.995192  \
1                     BPI_Challenge_2018                       0.649570   
2                   Receipt_WABO_CoSeLoG                       0.080893   
3                               BPIC15_3                       0.957417   
4                     BPI_Challenge_2019                       0.047562   
5                      RequestForPayment                       0.012925   
6                      PrepaidTravelCost                       0.096236   
7                   DomesticDeclarations                       0.009429   
8                               BPIC15_4                       0.996201   
9                     BPI_Challenge_2012                       0.333614   
10                          Hospital_log                       0.858268   
11                              BPIC15_5                       0.997405   
12                        CoSeLoG_WABO_2                       0.998450   
13  Road_Traffic_Fine_Management_Process                       0.001536   
14          BPI_Challenge_2017_Offer_log                       0.000372   
15                Sepsis_Cases_Event_Log                       0.805714   
16                        CoSeLoG_WABO_3                       0.949402   
17    BPI_Challenge_2013_closed_problems                       0.123067   
18          BPI_Challenge_2013_incidents                       0.200026   
19                             PermitLog                       0.209200   
20                              BPIC15_1                       0.975813   
21             InternationalDeclarations                       0.116762   
22                    BPI_Challenge_2017                       0.505570   
23                    BPI2016_Complaints                       0.438053   
24                     BPI2016_Questions                       0.797427   
25              BPI2016_Werkmap_Messages                       0.002882   
26      BPI_Challenge_2013_open_problems                       0.131868   
27                        CoSeLoG_WABO_1                       0.977588   
28                        CoSeLoG_WABO_4                       0.992376   
29                        CoSeLoG_WABO_5                       0.985426   
30                         Detail_Change                       0.048444   
31              Detail_Incident_Activity                       0.496847   
32                    Detail_Interaction                       0.000041   
33                                finale                       0.049345   

    ratio_most_common_variant  ratio_top_10_variants   
0                    0.002404               0.103365  \
1                    0.026981               0.415371   
2                    0.497211               0.887029   
3                    0.010646               0.137686   
4                    0.199758               0.946368   
5                    0.437264               0.933488   
6                    0.271081               0.822773   
7                    0.439810               0.950095   
8                    0.002849               0.102564   
9                    0.262016               0.686254   
10                   0.035871               0.227472   
11                   0.001730               0.102076   
12                   0.003101               0.100775   
13                   0.375620               0.993104   
14                   0.380626               0.380626   
15                   0.033333               0.274286   
16                   0.011960               0.145354   
17                   0.331540               0.840619   
18                   0.232195               0.794414   
19                   0.135315               0.757537   
20                   0.006672               0.121768   
21                   0.212281               0.811289   
22                   0.033514               0.531340   
23                   0.101770               0.424779   
24         

In [29]:
#Features between 0 and 1: 
def write_generator_bpic_experiment(objectives, n_para_obj=2):
    parameters_o = "objectives, "
    experiments = eval(f"[exp for exp in list(itertools.product({(parameters_o*n_para_obj)[:-2]})) if exp[0]!=exp[1]]")
    experiments = list(set([tuple(sorted(exp)) for exp in experiments]))
    for exp in experiments:
        experiment_path = os.path.join('..','data', '34_bpic_features')
        os.makedirs(experiment_path, exist_ok=True)
        experiment_path = os.path.join(experiment_path, f"34bpic_{len(exp)}objectives_{abbrev_obj_keys(exp)}.csv") 


        first_dir = os.path.split(experiment_path[3:])[-1].replace(".csv","")
        second_dir = first_dir.replace("grid_","").replace("objectives","")

        experiment = [
          {
            'pipeline_step': 'event_logs_generation',
            'output_path':'output/generated',
            'generator_params': {
              "experiment": {"input_path": "data/34_bpic_features.csv",
                "objectives": exp},
              'config_space': {
                'mode': [5, 20],
                'sequence': [0.01, 1],
                'choice': [0.01, 1],
                'parallel': [0.01, 1],
                'loop': [0.01, 1],
                'silent': [0.01, 1],
                'lt_dependency': [0.01, 1],
                'num_traces': [10, 10001],
                'duplicate': [0],
                'or': [0]
              },
              'n_trials': 200
            }
          },
          {
            'pipeline_step': 'feature_extraction',
            'input_path': os.path.join('output', 'features', 'generated', '34_bpic_features', second_dir),
            'feature_params': {'feature_set':['simple_stats', 'trace_length', 'trace_variant', 'activities', 'start_activities', 'end_activities', 'eventropies', 'epa_based']},
            'output_path': 'output/plots',
            'real_eventlog_path': 'data/34_bpic_features.csv',
            'plot_type': 'boxplot'
      }
        ]

        output_path = os.path.join('..', 'config_files','algorithm','34_bpic_features')
        os.makedirs(output_path, exist_ok=True)
        output_path = os.path.join(output_path, f'generator_{os.path.split(experiment_path)[-1].split(".")[0]}.json') 

        with open(output_path, 'w') as f:
            json.dump(experiment, f, ensure_ascii=False)
        print(f"Saved experiment config in {output_path}")
        return experiment


def create_objectives_grid(objectives, n_para_obj=2):
    parameters_o = "objectives, "
    experiments = eval(f"[exp for exp in list(itertools.product({(parameters_o*n_para_obj)[:-2]})) if exp[0]!=exp[1]]")
    experiments = list(set([tuple(sorted(exp)) for exp in experiments]))
    print(len(experiments))
    
    for exp in experiments:
        write_generator_bpic_experiment(objectives=exp)
        
exp_test = create_objectives_grid(normalized_feature_names, n_para_obj=2)        
print(exp_test)

21
Saved experiment config in ../config_files/algorithm/34_bpic_features/generator_34bpic_2objectives_enself_rt10v.json
Saved experiment config in ../config_files/algorithm/34_bpic_features/generator_34bpic_2objectives_enseef_rmcv.json
Saved experiment config in ../config_files/algorithm/34_bpic_features/generator_34bpic_2objectives_ense_enself.json
Saved experiment config in ../config_files/algorithm/34_bpic_features/generator_34bpic_2objectives_enve_rt10v.json
Saved experiment config in ../config_files/algorithm/34_bpic_features/generator_34bpic_2objectives_ense_rt10v.json
Saved experiment config in ../config_files/algorithm/34_bpic_features/generator_34bpic_2objectives_ense_enseef.json
Saved experiment config in ../config_files/algorithm/34_bpic_features/generator_34bpic_2objectives_enself_rmcv.json
Saved experiment config in ../config_files/algorithm/34_bpic_features/generator_34bpic_2objectives_rmcv_rutpt.json
Saved experiment config in ../config_files/algorithm/34_bpic_features/g

## Single objective from real logs
(Feature selection)

In [3]:
def write_single_objective_experiment(experiment_path, objectives=["ratio_top_20_variants", "epa_normalized_sequence_entropy_linear_forgetting"]):
    first_dir = os.path.split(experiment_path[3:])[-1].replace(".csv","")
    second_dir = first_dir.replace("grid_","").replace("objectives","")

    experiment = [
      {
        'pipeline_step': 'event_logs_generation',
        'output_path':os.path.join('output','generated', 'grid_1obj'),
        'generator_params': {
          "experiment": {"input_path": experiment_path[3:],
            "objectives": objectives},
          'config_space': {
            'mode': [5, 20],
            'sequence': [0.01, 1],
            'choice': [0.01, 1],
            'parallel': [0.01, 1],
            'loop': [0.01, 1],
            'silent': [0.01, 1],
            'lt_dependency': [0.01, 1],
            'num_traces': [10, 10001],
            'duplicate': [0],
            'or': [0]
          },
          'n_trials': 200
        }
      },
      {
        'pipeline_step': 'feature_extraction',
        'input_path': os.path.join('output','features', 'generated', 'grid_1obj', first_dir, second_dir),
        'feature_params': {'feature_set':['simple_stats', 'trace_length', 'trace_variant', 'activities', 'start_activities', 'end_activities', 'eventropies', 'epa_based']},
        'output_path': 'output/plots',
        'real_eventlog_path': 'data/34_bpic_features.csv',
        'plot_type': 'boxplot'
  }
    ]

    #print("EXPERIMENT:", experiment)
    output_path = os.path.join('..', 'config_files','algorithm','grid_experiments')
    os.makedirs(output_path, exist_ok=True)
    output_path = os.path.join(output_path, f'generator_{os.path.split(experiment_path)[-1].split(".")[0]}.json') 
    with open(output_path, 'w') as f:
        json.dump(experiment, f, ensure_ascii=False)
    print(f"Saved experiment config in {output_path}")
    
    return experiment

def create_objectives_grid(objectives, n_para_obj=2):
    parameters_o = "objectives, "
    if n_para_obj==1:
        experiments = [[exp] for exp in objectives]
    else:
        experiments = eval(f"[exp for exp in list(itertools.product({(parameters_o*n_para_obj)[:-2]})) if exp[0]!=exp[1]]")
    experiments = list(set([tuple(sorted(exp)) for exp in experiments]))
    print(len(experiments), "experiments: ", experiments)
    
    parameters = "np.around(np.arange(0, 1.1,0.1),2), "
    tasks = eval(f"list(itertools.product({(parameters*n_para_obj)[:-2]}))")
    tasks = [(f'task_{i+1}',)+task for i, task in enumerate(tasks)]
    print(len(tasks))
    for exp in experiments:
        df = pd.DataFrame(data=tasks, columns=["task", *exp])
        experiment_path = os.path.join('..','data', 'grid_experiments')
        os.makedirs(experiment_path, exist_ok=True)
        experiment_path = os.path.join(experiment_path, f"grid_{len(df.columns)-1}objectives_{abbrev_obj_keys(exp)}.csv") 
        df.to_csv(experiment_path, index=False)
        print(f"Saved experiment in {experiment_path}")
        write_single_objective_experiment(experiment_path, objectives=exp)
    #df.to_csv(f"../data/grid_{}objectives_{abbrev_obj_keys(objectives.tolist())}.csv" ,index=False)
        
exp_test = create_objectives_grid(normalized_feature_names, n_para_obj=1)        
print(exp_test)

7 experiments:  [('epa_normalized_sequence_entropy_exponential_forgetting',), ('epa_normalized_variant_entropy',), ('ratio_top_10_variants',), ('epa_normalized_sequence_entropy',), ('epa_normalized_sequence_entropy_linear_forgetting',), ('ratio_most_common_variant',), ('ratio_unique_traces_per_trace',)]
11
Saved experiment in ../data/grid_experiments/grid_1objectives_enseef.csv
Saved experiment config in ../config_files/algorithm/grid_experiments/generator_grid_1objectives_enseef.json
Saved experiment in ../data/grid_experiments/grid_1objectives_enve.csv
Saved experiment config in ../config_files/algorithm/grid_experiments/generator_grid_1objectives_enve.json
Saved experiment in ../data/grid_experiments/grid_1objectives_rt10v.csv
Saved experiment config in ../config_files/algorithm/grid_experiments/generator_grid_1objectives_rt10v.json
Saved experiment in ../data/grid_experiments/grid_1objectives_ense.csv
Saved experiment config in ../config_files/algorithm/grid_experiments/generator_g